# RAPIDS & Scanpy Single-Cell RNA-seq Multi-GPU Workflow on 1 Million Cells

Copyright (c) 2020, NVIDIA CORPORATION.

Licensed under the Apache License, Version 2.0 (the "License") you may not use this file except in compliance with the License. You may obtain a copy of the License at

    http://www.apache.org/licenses/LICENSE-2.0 

Unless required by applicable law or agreed to in writing, software distributed under the License is distributed on an "AS IS" BASIS, WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied. See the License for the specific language governing permissions and limitations under the License.

This notebook demonstrates a single-cell RNA analysis workflow that begins with preprocessing a count matrix of size `(n_gene, n_cell)` and results in a visualization of the clustered cells for further analysis.

For demonstration purposes, we use a dataset of 1M brain cells with Unified Virtual Memory to oversubscribe GPU memory. We then use dask to scale PCA, K-means clustering, and UMAP across multiple GPUs.

See the README for instructions to download this dataset.

## Import requirements

In [1]:
import time
import pandas as pd
import numpy as np
import scanpy as sc
import anndata

import matplotlib.pyplot as plt
import matplotlib.animation as animation
from natsort import natsorted

import cupy as cp
import cupyx as cpx
import cupyx
import cugraph

import cudf
import math

import h5py
import scipy

import dask
import dask_cudf
import rmm

from dask_cuda import initialize, LocalCUDACluster
from dask import delayed, dataframe
from dask.dataframe.utils import make_meta
from dask.distributed import Client, default_client
from dask_cuda.local_cuda_cluster import cuda_visible_devices
import dask.dataframe as dd

from cuml.manifold import TSNE, UMAP
from cuml.linear_model import LinearRegression

from cuml.dask.decomposition import PCA as cu_dask_PCA
from cuml.dask.cluster import KMeans as cu_dask_KMeans
from cuml.dask.manifold import UMAP as cu_dask_UMAP
from cuml.dask.linear_model import LinearRegression as cu_dask_LinearRegression
from cuml.dask.neighbors import NearestNeighbors as cu_dask_NearestNeighbors

from bokeh.io.export import export_png
from bokeh.models.tickers import FixedTicker
from bokeh.io import output_notebook

import rapids_scanpy_funcs
import utils

import warnings
warnings.filterwarnings('ignore', 'Expected ')
warnings.simplefilter('ignore')

output_notebook()

Loading BokehJS ...

We use the RAPIDS memory manager to enable Unified Virtual Memory management, which allows us to oversubscribe the GPU memory

In [2]:
cluster_start = time.time()

enable_tcp_over_ucx = True
enable_nvlink = True
enable_infiniband = True
CUDA_VISIBLE_DEVICES = cuda_visible_devices(0).split(',')
CUDA_VISIBLE_DEVICES = [1, 2, 3, 4, 5, 6, 7]

rmm.reinitialize(managed_memory=False)
cp.cuda.set_allocator(rmm.rmm_cupy_allocator)

initialize.initialize(create_cuda_context=True,
                      enable_tcp_over_ucx=enable_tcp_over_ucx,
                      enable_nvlink=enable_nvlink,
                      enable_infiniband=enable_infiniband)

cluster = LocalCUDACluster(protocol="ucx",
                           dashboard_address=':9001',
                           CUDA_VISIBLE_DEVICES=CUDA_VISIBLE_DEVICES,
                           enable_tcp_over_ucx=enable_tcp_over_ucx,
                           enable_nvlink=enable_nvlink,
                           enable_infiniband=enable_infiniband)

client = Client(cluster)
client.run(cp.cuda.set_allocator)
n_workers = len(client.scheduler_info()['workers'].keys())
client

<Client: 'ucx://127.0.0.1:53275' processes=7 threads=7, memory=540.95 GB>

## Input data

In the cell below, we provide the path to the sparse `.h5ad` file containing the count matrix to analyze. Please see the README for instructions on how to download the dataset we use here.

To run this notebook using your own dataset, please see the README for instructions to convert your own count matrix into this format. Then, replace the path in the cell below with the path to your generated `.h5ad` file.

In [3]:
import os, wget

input_file = "../data/1M_brain_cells_10X.sparse.h5ad"
if not os.path.exists(input_file):
    print('Downloading import file...')
    os.makedirs('../data', exist_ok=True)
    wget.download(
        'https://rapids-single-cell-examples.s3.us-east-2.amazonaws.com/1M_brain_cells_10X.sparse.h5ad',
        input_file)

## Set parameters

In [4]:
# marker genes
MITO_GENE_PREFIX = "mt-"              # Prefix for mitochondrial genes to regress out
markers = ["Stmn2", "Hes1", "Olig1"]  # Marker genes for visualization

# filtering cells
min_genes_per_cell = 200      # Filter out cells with fewer genes than this expressed 
max_genes_per_cell = 6000     # Filter out cells with more genes than this expressed 
min_cells=1                   # Genes containing a number of cells below this value will be filtered

# filtering genesinitialize
n_top_genes = 4000            # Number of highly variable genes to retain

# PCA
n_components = 50             # Number of principal components to compute
pca_train_ratio = 0.35        # percentage of cells to use for PCA training
n_pca_batches = 10

# t-SNE
tsne_n_pcs = 20               # Number of principal components to use for t-SNE

# k-means
k = 35                        # Number of clusters for k-means

# KNN
n_neighbors = 15              # Number of nearest neighbors for KNN graph
knn_n_pcs = 50                # Number of principal components to use for finding nearest neighbors

# UMAP
umap_train_ratio = 0.35
umap_min_dist = 0.3
umap_spread = 1.0

max_cells = 100000            # To filter first x numbers of rows. Please change it to -1 for using all
BATCHSIZE = 20000

start_time = time.time()

## Load and Prepare Data

## We load the sparse count matrix from an `h5ad` file using Scanpy. The sparse count matrix will then be placed on the GPU. 

In [5]:
time_data_load = time.time()

In [6]:
%%time

with h5py.File(input_file, 'r') as h5f:
    indptr = h5f['/X/indptr']
    orginal_genes = cudf.Series(h5f['/var/_index'], dtype=cp.dtype('object'))
    total_cols = orginal_genes.shape[0]
    total_rows = indptr.shape[0] - 1

if max_cells <= 0:
    max_cells = total_rows

def partition_postprocessor_sum(partial_sparse_array):
    partial_sparse_sq_array = partial_sparse_array.power(2)
    col1 = partial_sparse_array.sum(axis=0)
    col2 = partial_sparse_sq_array.sum(axis=0)
    ret_value = cp.hstack([col1, col2])

    del partial_sparse_sq_array

    return ret_value
    
print('Computing data required to create filter...')
aggregated_mat = utils.read_to_sparse_matrix(input_file,
                                       max_cells, BATCHSIZE, total_cols * 2,
                                       None, partition_postprocessor_sum,
                                       min_genes_per_cell=min_genes_per_cell,
                                       max_genes_per_cell=max_genes_per_cell)
aggregated_mat = aggregated_mat.compute()

# Split the sum and square
sum_mat = aggregated_mat[:, 0:aggregated_mat.shape[1]/2].sum(axis=0)
sum_sq_mat = aggregated_mat[:, aggregated_mat.shape[1]/2:]

# Filter genes with at-least <<min_cells>> number of cells rec.
min_cell_filter = (sum_mat >= min_cells)

sum_mat = sum_mat[min_cell_filter]
sum_sq_mat = sum_sq_mat[:, min_cell_filter].sum(axis=0)
genes = orginal_genes[min_cell_filter]

del aggregated_mat

print('Loading data into dataframes...')
sparse_dask_array = utils.read_to_sparse_matrix(input_file,
                                       max_cells, BATCHSIZE, sum_sq_mat.shape[0],
                                       min_cell_filter, None,
                                       min_genes_per_cell=min_genes_per_cell,
                                       max_genes_per_cell=max_genes_per_cell)

sparse_dask_array = sparse_dask_array.persist()
sparse_dask_array

Computing data required to create filter...
Loading data into dataframes...
CPU times: user 5.68 s, sys: 1.09 s, total: 6.78 s
Wall time: 14 s


dask.array<concatenate, shape=(100000, 21517), dtype=float32, chunksize=(20000, 21517), chunktype=numpy.ndarray>

For this example, we select the first 1 million cells in the dataset. We maintain the index of unique genes in our dataset:

Verify the shape of the resulting sparse matrix:

In [7]:
%%time
sparse_dask_array = dask.array.log1p(sparse_dask_array)

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 565 µs


And the number of non-zero values in the matrix:

In [8]:
time_data_load = time.time() - time_data_load
print("Total data load and Filtering: %s" % time_data_load)

Total data load and Filtering: 14.035927534103394


## Preprocessing

In [9]:
preprocess_start = time.time()

### Filter

We filter the count matrix to remove cells with an extreme number of genes expressed.

Some genes will now have zero expression in all cells. We filter out such genes.

In [10]:
%%time
# FILTERING IS NOT DONE WHILE READING DATA
# sparse_dask_array, genes = rapids_scanpy_funcs.filter_genes(sparse_dask_array, genes.get(), min_cells=1)

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 5.25 µs


The size of our count matrix is now reduced.

In [11]:
%%time
sparse_dask_array.shape

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 17.2 µs


(100000, 21517)

### Normalize

We normalize the count matrix so that the total counts in each cell sum to 1e4.

In [12]:
%%time
# This is now done while loading data
# sparse_dask_array = rapids_scanpy_funcs.normalize_total(sparse_dask_array, target_sum=1e4)

# sparse_dask_array = sparse_dask_array.astype(cp.float32)
# sparse_dask_array.shape

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 5.25 µs


Next, we log transform the count matrix.

In [13]:
%%time

marker_genes_raw = {}
genes = genes.reset_index(drop=True)
i = 0
for index in genes[genes.isin(markers)].index.to_arrow().to_pylist():
    marker_genes_raw[markers[i]] = sparse_dask_array[:, index].compute().toarray().ravel()
    i += 1

CPU times: user 440 ms, sys: 140 ms, total: 580 ms
Wall time: 2.09 s


### Select Most Variable Genes

We convert the count matrix to an annData object.

Before filtering the count matrix, we save the 'raw' expression values of the marker genes to use for labeling cells afterward.

Using scanpy, we filter the count matrix to retain only the most variable genes.

In [14]:
time_marker_highly_variable = time.time()

In [15]:
%%time
# gpu_array = sparse_dask_array.compute()
# adata = anndata.AnnData(gpu_array.get())
# adata.var_names = genes.to_pandas()

# sc.pp.highly_variable_genes(adata, n_top_genes=n_top_genes, flavor="cell_ranger")
# sc_hightly_variable = genes[adata.var.highly_variable.values]

vaiable_genes = utils.highly_variable_genes_filter(sum_mat, 
                                                   sum_sq_mat, 
                                                   sparse_dask_array, 
                                                   genes, 
                                                   n_top_genes=n_top_genes)
genes = genes[vaiable_genes]

# Filter highly variable genes
dask_array = sparse_dask_array[:, vaiable_genes]

CPU times: user 132 ms, sys: 12 ms, total: 144 ms
Wall time: 141 ms


In [16]:
time_marker_highly_variable = time.time() - time_marker_highly_variable
print("Highly variable genes: %s" % time_marker_highly_variable)

Highly variable genes: 0.15041351318359375


### Regress out confounding factors (number of counts, mitochondrial gene expression)

We can now perform regression on the count matrix to correct for confounding factors -  for example purposes, we use the number of counts and the expression of mitochondrial genes (named starting with `mt-`).

We now calculate the total counts and the percentage of mitochondrial counts for each cell.

In [17]:
%%time
time_regress_out = time.time()

sparse_dask_array = utils.csr_to_csc(dask_array, client=client)
sparse_dask_array = sparse_dask_array.persist()
sparse_dask_array.shape

CPU times: user 1.23 s, sys: 716 ms, total: 1.95 s
Wall time: 2.12 s


(99109, 4000)

In [18]:
%%time

mito_genes = genes.str.startswith(MITO_GENE_PREFIX)
mito_genes = cp.fromDlpack(mito_genes.to_dlpack())
mito_genes_indices = cp.where(mito_genes == 1)[0]

n_counts = utils.sum_csc(sparse_dask_array, client=client)
n_counts = dask.array.sum(n_counts, axis=1).compute()

result = dask.array.take(sparse_dask_array,
                         mito_genes_indices.tolist(),
                         axis=1)
result = utils.sum_csc(result, client=client)
result = dask.array.sum(result, axis=1)
result = dask.array.true_divide(result, n_counts)
# result.compute()

percent_mito = dask.array.ravel(result)
percent_mito = percent_mito.compute()
del result

CPU times: user 272 ms, sys: 64 ms, total: 336 ms
Wall time: 1.45 s


And perform regression:

In [19]:
%%time
regressors = cp.ones((n_counts.shape[0]*3), dtype=cp.float32).reshape((n_counts.shape[0], 3), order="F")
regressors[:, 1] = n_counts
regressors[:, 2] = percent_mito

X = dask.array.from_array(regressors, asarray=False)
del regressors
del n_counts
X.shape

CPU times: user 4 ms, sys: 4 ms, total: 8 ms
Wall time: 6.09 ms


(99109, 3)

In [20]:
%%time

# sparse_gpu_array = rapids_scanpy_funcs.regress_out(
#     sparse_gpu_array, n_counts, percent_mito)

def regress(regressors, arr, cols_per_task=10):
    
    @delayed
    def _regress(X, data):
        if hasattr(data, 'todense'):
            data = data.todense()

        outputs = cp.empty(data.shape, dtype=data.dtype, order="F")
        for i in range(data.shape[1]):
            y = data[:, i]
            lr = LinearRegression(fit_intercept=False, output_type="cupy")
            lr.fit(X, y, convert_dtype=True)
            outputs[:, i] = y.reshape(y.shape[0], ) - lr.predict(X).reshape(y.shape[0])
        del data
        return outputs

    print('Creating dask tasks for LinearRegression...')
    ld_delay = []

    for i in range(0, arr.shape[1], cols_per_task):
        y = arr[:, i:i+cols_per_task]
        ld_delay.append(
            dask.array.from_delayed(
                (_regress)(regressors, y),
                dtype=cp.float32,
                shape=(arr.shape[0], cols_per_task)))
        del y

    print('Computing...')
    result = dask.array.concatenate(ld_delay, axis=1)
    return result

sparse_dask_array = regress(X, sparse_dask_array, cols_per_task=20)
sparse_dask_array

Creating dask tasks for LinearRegression...
Computing...
CPU times: user 228 ms, sys: 52 ms, total: 280 ms
Wall time: 265 ms


dask.array<concatenate, shape=(99109, 4000), dtype=float32, chunksize=(99109, 20), chunktype=numpy.ndarray>

### Scale

Finally, we scale the count matrix to obtain a z-score and apply a cutoff value of 10 standard deviations, obtaining the preprocessed count matrix.

In [21]:
%%time
# sparse_gpu_array = rapids_scanpy_funcs.scale(sparse_gpu_array, max_value=10)

max_value=10

def scale(dask_array, client, max_value=10):
    mean = dask.array.mean(dask_array, axis=0)
    temp_array = dask.array.subtract(dask_array, mean)

    stddev = dask.array.sqrt(mean.var())
    temp_array = dask.array.true_divide(temp_array, stddev)
    dask_array = utils.clip(temp_array, client, max_value)

    del stddev
    del temp_array
    del mean
    
    return dask_array

sparse_dask_array = scale(sparse_dask_array, client, max_value=max_value)

CPU times: user 11.5 s, sys: 4.3 s, total: 15.8 s
Wall time: 49.7 s


In [22]:
time_regress_out = time.time() - time_regress_out
print("Regressout and scale: %s" % time_regress_out)

Regressout and scale: 53.56210780143738


## Cluster & Visualize

We store the preprocessed count matrix as an AnnData object, which is currently in host memory. We also add the expression levels of the marker genes as observations to the annData object.

### Reduce

We use PCA to reduce the dimensionality of the matrix to its top 50 principal components. Here, we use Dask to parallelize across multiple GPUs.

The PCA multi-GPU time includes initial data transfer, which is about 20gb. 

In [23]:
%%time

# dask_df = dask.dataframe.from_array(sparse_gpu_array, columns=gene.to_arrow().to_pylist())
# dask_cu_df = dask_cudf.from_dask_dataframe(dask_df)
#
# The above line does not work due to worker failure while converting sparse
# array to dataframes. Folloiwng code is a workaround for loading data using 
# delayed functions.

def pca(dask_array, n_components, client, n_workers):
    dask_cu_df = utils.sparse_array_to_df(dask_array, n_workers)

    pca_model = cu_dask_PCA(n_components=n_components, client=client)
    dask_reduced_df = pca_model.fit_transform(dask_cu_df)

    reduced_df = dask_reduced_df.compute()
    return dask_cu_df, reduced_df

dask_cu_df, reduced_df = pca(sparse_dask_array, n_components, client, n_workers)
reduced_df = reduced_df.reindex(range(reduced_df.shape[0]))
print(reduced_df.shape)

Number of records is 99109 and batch size is 14159
Creating dask df from delays...
Creating Dataframe from futures...
(99109, 50)
CPU times: user 7.66 s, sys: 464 ms, total: 8.13 s
Wall time: 16.7 s


In [24]:
# reduced_df.to_hdf('/data/reduced.hdf5', 'reduced')
time_data_load, time_marker_highly_variable, time_regress_out

(14.035927534103394, 0.15041351318359375, 53.56210780143738)

### t-SNE + k-Means

We cluster the cells using k-means on the principal components. For example purposes, we set k=35.

In [25]:
%%time
# dask_array.head(20)
tsne = TSNE().fit_transform(reduced_df.iloc[:, :tsne_n_pcs])

[W] [09:35:07.353712] # of Nearest Neighbors should be at least 3 * perplexity. Your results might be a bit strange...
CPU times: user 1.25 s, sys: 1.44 s, total: 2.69 s
Wall time: 2.67 s


In [26]:
%%time
# K-means
dask_array = dask_cudf.from_cudf(reduced_df, npartitions=n_workers*10)
dask_kmeans = cu_dask_KMeans(n_clusters=k)
dask_kmeans.fit(dask_array)
labels = dask_kmeans.predict(dask_array).compute()
labels.index = reduced_df.index

CPU times: user 1.74 s, sys: 176 ms, total: 1.92 s
Wall time: 3.02 s


We visualize the cells using t-SNE and label cells by color according to the k-means clustering.

In [27]:
%%time

tsne['kmeans'] = labels
utils.show_scatter(tsne, 0, 1, 'kmeans', 'kmeans')

# sc.pl.tsne(adata, color=["kmeans"])
# x_embedded = TSNE().fit_transform(sparse_gpu_array)

CPU times: user 5.13 s, sys: 116 ms, total: 5.24 s
Wall time: 5.04 s


We label the cells using the `Stmn2` and `Hes1` marker genes, for neuronal and glial cells respectively. These visualizations show us the separation of neuronal and glial cells on the t-SNE plot.

In [28]:
%%time

for marker_gene in marker_genes_raw:
    tsne[marker_gene + '_raw'] = marker_genes_raw[marker_gene]

utils.show_scatter_grad(tsne, 0, 1, 'Stmn2_raw', 'Stmn2')
utils.show_scatter_grad(tsne, 0, 1, 'Hes1_raw', 'Hes1')

del dask_array, tsne, dask_kmeans, labels, reduced_df
# sc.pl.tsne(adata, color=["Stmn2_raw"], color_map="Blues", vmax=1, vmin=-0.05)
# sc.pl.tsne(adata, color=["Hes1_raw"], color_map="Blues", vmax=1, vmin=-0.05)

CPU times: user 420 ms, sys: 4 ms, total: 424 ms
Wall time: 414 ms


### UMAP + Graph clustering

We can also visualize the cells using the UMAP algorithm in Rapids. Before UMAP, we need to construct a k-nearest neighbors graph in which each cell is connected to its nearest neighbors. This can be done conveniently using rapids functionality already integrated into Scanpy.

Note that Scanpy uses an approximation to the nearest neighbors on the CPU while the GPU version performs an exact search. While both methods are known to yield useful results, some differences in the resulting visualization and clusters can be observed.

The UMAP function from Rapids is also integrated into Scanpy.

Finally, we use the Louvain algorithm for graph-based clustering, once again using the `rapids` option in Scanpy.

In [29]:
%%time
# sc.pp.neighbors(adata, n_neighbors=n_neighbors, n_pcs=knn_n_pcs, method='rapids')
# sc.tl.umap(adata, min_dist=umap_min_dist, spread=umap_spread, method='rapids')

tranining_data = sparse_dask_array[:int(max_cells * umap_train_ratio)].compute()
local_model = UMAP(n_epochs=1000, min_dist=umap_min_dist, spread=umap_spread, local_connectivity=1.0)
local_model.fit(tranining_data)

dist_model = cu_dask_UMAP(local_model,
                          min_dist=umap_min_dist,
                          spread=umap_spread,
                          local_connectivity=1.0)
X_umap = dist_model.transform(dask_cu_df)
del tranining_data, dask_cu_df

CPU times: user 5.38 s, sys: 2.83 s, total: 8.21 s
Wall time: 11.6 s


In [31]:
from cuml.neighbors import NearestNeighbors

test = sparse_dask_array.compute()

nn_model = NearestNeighbors(n_neighbors=n_neighbors, output_type="input")
nn_model.fit(test)
connectivity_mat = nn_model.kneighbors_graph(X=test, n_neighbors=n_neighbors, mode='connectivity') 

We plot the cells using the UMAP visualization, and using the Louvain clusters as labels.

In [32]:
%%time
# sc.tl.louvain(adata, flavor='rapids')

offsets = cudf.Series(connectivity_mat.indptr)
indices = cudf.Series(connectivity_mat.indices)
g = cugraph.Graph()

if hasattr(g, 'add_adj_list'):
    g.add_adj_list(offsets, indices, None)
else:
    g.from_cudf_adjlist(offsets, indices, None)

louvain_parts, _ = cugraph.louvain(g)

umap_df = X_umap.compute()
umap_df = umap_df.reindex(index=range(umap_df.shape[0]))

groups = louvain_parts.sort_values('vertex')['partition']
groups = cp.fromDlpack(groups.to_dlpack())
umap_df['louvain_group'] = cudf.Series(groups)

CPU times: user 2.57 s, sys: 1.01 s, total: 3.58 s
Wall time: 9.59 s


In [33]:
%%time
# sc.pl.umap(adata, color=["louvain"])
utils.show_scatter(umap_df, 0, 1, 'louvain_group', 'louvain')

CPU times: user 1.92 s, sys: 40 ms, total: 1.96 s
Wall time: 1.88 s


In [34]:
%%time
# adata.obs['leiden'] = rapids_scanpy_funcs.leiden(adata)

leiden_parts, _ = cugraph.leiden(g)

groups = leiden_parts.sort_values('vertex')['partition']
groups = cp.fromDlpack(groups.to_dlpack())
umap_df['leiden_group'] = cudf.Series(groups)

utils.show_scatter(umap_df, 0, 1, 'leiden_group', 'leiden')

CPU times: user 2.02 s, sys: 28 ms, total: 2.05 s
Wall time: 1.97 s


And also visualize the cells labeled by expression of the `Stmn2` and `Hes1` marker genes, for neuronal and glial cells respectively.

In [35]:
%%time
# sc.pl.umap(adata, color=["Stmn2_raw"], color_map="Blues", vmax=1, vmin=-0.05)
# sc.pl.umap(adata, color=["Hes1_raw"], color_map="Blues", vmax=1, vmin=-0.05)

for marker_gene in marker_genes_raw:
    umap_df[marker_gene + '_raw'] = marker_genes_raw[marker_gene]

utils.show_scatter_grad(umap_df, 0, 1, 'Stmn2_raw', 'Stmn2')
utils.show_scatter_grad(umap_df, 0, 1, 'Hes1_raw', 'Hes1')

CPU times: user 460 ms, sys: 8 ms, total: 468 ms
Wall time: 455 ms


In [36]:
cluster_time = time.time()
print("Total cluster time : %s" % (cluster_time-cluster_start))

Total cluster time : 167.5140471458435


## Create Zoomed View

The speedup offered by Rapids makes it easy to interactively re-analyze subsets of cells. To illustrate this, we select glial cells (Hes1+) from the dataset.

In [ ]:
reanalysis_start = time.time()

In [ ]:
%%time
hes1_cells = marker_genes_raw["Hes1_raw"] > 0.0
adata = adata[hes1_cells.get(),:]
adata.shape

We can repeat the dimension reduction, clustering and visualization using this subset of cells in seconds. 

Finally, we visualize the selected neuronal cells labeled by their new clusters, and by the expression of `Olig1`, a marker gene for oligodendrocytes.

In [ ]:
del dask_array

In [ ]:
%%time

chunk_size = int(sparse_dask_array.shape[0] / (n_workers*10))
dask_array = dask.array.from_array(cp.asarray(adata.X), 
                                   chunks=(chunk_size, -1))
dask_array = dask_array.persist()

client.rebalance()

In [ ]:
%%time
dask_array = pca.fit_transform(dask_array)
adata.obsm['X_pca'] = dask_array.compute().get()

In [ ]:
%%time
sc.pp.neighbors(adata, n_neighbors=n_neighbors, n_pcs=knn_n_pcs, method='rapids')
sc.tl.umap(adata, min_dist=umap_min_dist, spread=umap_spread, method='rapids')
sc.tl.louvain(adata, flavor='rapids')

In [ ]:
%%time
sc.pl.umap(adata, color=["louvain"])
sc.pl.umap(adata, color=["Olig1_raw"], color_map="Blues", vmax=1, vmin=-0.05)

In [ ]:
reanalysis_time = time.time()
print("Total reanalysis time : %s" % (reanalysis_time-reanalysis_start))

In [ ]:
print("Full time: %s" % (time.time() - start_time))
# client.close()